# Travaux pratiques sur les réseaux d'eau

## 0. Données et fonctions du problème

### On charge dans l'environnement :
1. les fonctions de Julia qui seront utilisées,
2. les données du problème,
3. les fonctions utilitaires du problème.

In [ ]:
using LinearAlgebra
using PyPlot

In [ ]:
include("Probleme_R.jl")
include("Structures_N.jl")
println()
println("Tailles du reseau etudie")
println("Nombre de tuyaux  : ", n)
println("Nombre de noeuds  : ", m)

In [ ]:
include("Visualg.jl")
include("Verification.jl")

###  On charge les prototypes d'algorithmes d'optimisation :

* **Gradient_F** : algorithme de gradient à pas fixe,
* **Newton_F** : algorithme de Newton à pas fixe.

In [ ]:
function Gradient_F(Oracle, x0, alpha0)

  ##### Initialisation des variables

  iter   = 10000
  alphai = alpha0
  tol    = 1e-6

  nx = length(x0)
  
  logG = Float64[]
  logP = Float64[]
  cout = Float64[]
    
  F = Inf
  G = zeros(Float64, nx)
  D = zeros(Float64, nx)

  x = copy(x0)

  ##### Boucle sur les iterations

  tic = time()

  kstar = iter
  for k = 1:iter

      # Appel de l'oracle
      F, G = Oracle(x)

      # Test de convergence
      if norm(G) <= tol
          kstar = k
          break
      end

      # Direction de descente
      D = -G

      # Calcul du pas de gradient
      alphan = alphai

      # Mise a jour du point courant
      x = x + (alphan*D)

      # Evolution du gradient, du pas et du critere
      push!(logG, log10(norm(G)))
      push!(logP, log10(alphan))
      push!(cout, F)

  end

  ##### Resultats de l'optimisation
    
  fopt = F
  gopt = G
  xopt = x
  tcpu = time() - tic
    
  println()
  println("Iteration : ", kstar)
  println("Temps CPU : ", tcpu)
  println("Critere optimal : ", fopt)
  println("Norme du gradient : ", norm(G))

  # Visualisation de la convergence
  Visualg(logG, logP, cout)
    
  return fopt, gopt, xopt
    
end

In [ ]:
function Newton_F(Oracle, x0, alpha0)

  ##### Initialisation des variables

  iter   = 100
  alphai = alpha0
  tol    = 1e-6

  nx = length(x0)
  
  logG = Float64[]
  logP = Float64[]
  cout = Float64[]

  F = Inf
  G = zeros(Float64, nx)
  H = zeros(Float64, nx, nx)
  D = zeros(Float64, nx)

  x = copy(x0)

  ##### Boucle sur les iterations

  tic = time()

  kstar = iter
  for k = 1:iter

      # Appel de l'oracle
      F, G, H = Oracle(x)

      # Test de convergence
      if norm(G) <= tol
          kstar = k
          break
      end

      # Direction de descente
      D = - H \ G

      # Test de la direction de descente
      coe = D' * G
      if coe >= 0.0
          D = -G
          #println("Direction de montee --- iteration ", k)
      end

      # Calcul du pas de gradient
      alphan = alphai

      # Mise a jour du point courant
      x = x + (alphan*D)

      # Evolution du gradient, du pas et du critere

      push!(logG, log10(norm(G)))
      push!(logP, log10(alphan))
      push!(cout, F)

  end

  ##### Resultats de l'optimisation

  fopt = F
  gopt = G  
  xopt = x
  tcpu = time() - tic
    
  println()
  println("Iteration : ", kstar)
  println("Temps CPU : ", tcpu)
  println("Critere optimal : ", fopt)
  println("Norme du gradient : ", norm(G))

  # Visualisation de la convergence
  Visualg(logG, logP, cout)
    
  return fopt, gopt, xopt
    
end

## I. Résolution du problème primal

In [ ]:
include("HydrauliqueP.jl")

### I.a On écrit les oracles pour le problème primal d'optimisation :

* **OraclePG** : calcul de la fonction et du gradient,
* **OraclePH** : calcul de la fonction du gradient et du Hessien.

In [ ]:
function OraclePG(qc)

  # ---> A COMPLETER
  # ---> A COMPLETER

  return F, G

end

In [ ]:
function OraclePH(qc)

  # ---> A COMPLETER
  # ---> A COMPLETER

  return F, G, H

end

### On teste la validité des oracles en résolvant le problème :

* **OraclePG** avec la méthode du gradient à pas fixe,
* **OraclePH** avec la méthode de Newton à pas fixe

In [ ]:
x0 = 0.1 * rand(n-md)
println()
println("MINIMISATION DU PROBLEME PRIMAL")
println()
println("ALGORITHME DU GRADIENT A PAS FIXE")
copt, gopt, xopt = Gradient_F(OraclePG, x0, 0.0005)
qopt, zopt, fopt, popt = HydrauliqueP(xopt)
Verification(qopt, zopt, fopt, popt)

In [ ]:
x0 = 0.1 * rand(n-md)
println()
println("MINIMISATION DU PROBLEME PRIMAL")
println()
println("ALGORITHME DE NEWTON A PAS FIXE")
copt, gopt, xopt = Newton_F(OraclePH, x0, 1.0)
qopt, zopt, fopt, popt = HydrauliqueP(xopt)
Verification(qopt, zopt, fopt, popt)

### I.b On écrit l'algorithme de recherche linéaire (conditions de Wolfe).

In [ ]:
function Wolfe(alpha, x, D, Oracle)

    ##### Coefficients de la recherche lineaire

    omega1 = 0.1
    omega2 = 0.9

    alphamin = 0.0
    alphamax = Inf

    ok = 0
    dltx = 0.00000001

    ##### Algorithme de Fletcher-Lemarechal

    # Appel de l'oracle au point initial
    F, G = Oracle(x)

    # Initialisation de l'algorithme
    alphan = alpha
    xn = copy(x)
    xp = copy(x)
    Gn = zeros(Float64, length(x))
    
    # Boucle de calcul du pas
    # xn represente le point pour la valeur courante du pas,
    # xp represente le point pour la valeur precedente du pas.
    while ok == 0

        # Point precedent pour tester l'indistinguabilite
        xp[:] = xn

        # Point actuel
        xn[:] = x .+ alphan*D

        # Calcul des conditions de Wolfe
        #
        # ---> A COMPLETER
        # ---> A COMPLETER
        
        # Test des conditions de Wolfe
        # - Si les deux conditions de Wolfe sont verifiees,
        #   poser ok = 1 : on sort alors de la boucle while
        # - Sinon, modifier la valeur de alphan et reboucler
        #
        # ---> A COMPLETER
        # ---> A COMPLETER

        #  Test d'indistingabilite
        if norm(xn-xp) < dltx
            ok = 2
        end
    end

    return alphan
    
end

### I.c On écrit l'algorithme du gradient à pas variable et on le teste

In [ ]:
function Gradient_V(Oracle, x0, alpha0)

  ##### Initialisation des variables

  iter   = 1000
  alphai = alpha0
  tol    = 1e-6

  nx = length(x0)
  
  logG = Float64[]
  logP = Float64[]
  cout = Float64[]
    
  F = Inf
  G = zeros(Float64, nx)
  D = zeros(Float64, nx)

  x = copy(x0)

  ##### Boucle sur les iterations

  tic = time()

  kstar = iter
  for k = 1:iter

      # ---> A COMPLETER
      # ---> A COMPLETER

  end

  ##### Resultats de l'optimisation
    
  fopt = F
  gopt = G
  xopt = x
  tcpu = time() - tic
    
  println()
  println("Iteration : ", kstar)
  println("Temps CPU : ", tcpu)
  println("Critere optimal : ", fopt)
  println("Norme du gradient : ", norm(G))

  # Visualisation de la convergence
  Visualg(logG, logP, cout)
    
  return fopt, gopt, xopt
    
end

In [ ]:
x0 = 0.1 * rand(n-md)
println()
println("MINIMISATION DU PROBLEME PRIMAL")
println()
println("ALGORITHME DU GRADIENT A PAS VARIABLE")
copt, gopt, xopt = Gradient_V(OraclePG, x0, 1.0)
qopt, zopt, fopt, popt = HydrauliqueP(xopt)
Verification(qopt, zopt, fopt, popt)

### I.d On écrit l'algorithme de gradient conjugué (Polak-Ribière) et on le teste

In [ ]:
function PolakRibiere(Oracle, x0, alpha0)

  ##### Initialisation des variables

  iter   = 1000
  alphai = alpha0
  tol    = 1e-6

  nx = length(x0)
  
  logG = Float64[]
  logP = Float64[]
  cout = Float64[]
    
  F = Inf
  G = zeros(Float64, nx)
  D = zeros(Float64, nx)

  x = copy(x0)

  ##### Boucle sur les iterations

  tic = time()

  kstar = iter
  for k = 1:iter

      # ---> A COMPLETER
      # ---> A COMPLETER
      #
      # Attention a l'initialisation de l'algorithme !

  end

  ##### Resultats de l'optimisation
    
  fopt = F
  gopt = G
  xopt = x
  tcpu = time() - tic
    
  println()
  println("Iteration : ", kstar)
  println("Temps CPU : ", tcpu)
  println("Critere optimal : ", fopt)
  println("Norme du gradient : ", norm(G))

  # Visualisation de la convergence
  Visualg(logG, logP, cout)
    
  return fopt, gopt, xopt
    
end

In [ ]:
x0 = 0.1 * rand(n-md)
println()
println("MINIMISATION DU PROBLEME PRIMAL")
println()
println("ALGORITHME DU GRADIENT CONJUGUE")
copt, gopt, xopt = PolakRibiere(OraclePG, x0, 1.0)
qopt, zopt, fopt, popt = HydrauliqueP(xopt)
Verification(qopt, zopt, fopt, popt)

### I.e On écrit l'algorithme de quasi-Newton (BFGS) et on le teste

In [ ]:
function BFGS(Oracle, x0, alpha0)

  ##### Initialisation des variables

  iter   = 250
  alphai = alpha0
  tol    = 1e-6

  nx = length(x0)
  
  logG = Float64[]
  logP = Float64[]
  cout = Float64[]
    
  F = Inf
  G = zeros(Float64, nx)
  D = zeros(Float64, nx)

  x = copy(x0)

  ##### Boucle sur les iterations

  tic = time()

  kstar = iter
  for k = 1:iter

      # ---> A COMPLETER
      # ---> A COMPLETER
      #
      # Attention a l'initialisation de l'algorithme !
      
  end

  ##### Resultats de l'optimisation
    
  fopt = F
  gopt = G
  xopt = x
  tcpu = time() - tic
    
  println()
  println("Iteration : ", kstar)
  println("Temps CPU : ", tcpu)
  println("Critere optimal : ", fopt)
  println("Norme du gradient : ", norm(G))

  # Visualisation de la convergence
  Visualg(logG, logP, cout)
    
  return fopt, gopt, xopt

end

In [ ]:
x0 = 0.1 * rand(n-md)
println()
println("MINIMISATION DU PROBLEME PRIMAL")
println()
println("ALGORITHME DE QUASI-NEWTON")
copt, gopt, xopt = BFGS(OraclePG, x0, 1.0)
qopt, zopt, fopt, popt = HydrauliqueP(xopt)
Verification(qopt, zopt, fopt, popt)

### I.f On écrit l'algorithme de Newton à pas variable et on le teste

In [ ]:
function Newton_V(Oracle, x0, alpha0)

  ##### Initialisation des variables

  iter   = 100
  alphai = alpha0
  tol    = 1e-6

  nx = length(x0)
  
  logG = Float64[]
  logP = Float64[]
  cout = Float64[]

  F = Inf
  G = zeros(Float64, nx)
  H = zeros(Float64, nx, nx)
  D = zeros(Float64, nx)

  x = copy(x0)

  ##### Boucle sur les iterations

  tic = time()

  kstar = iter
  for k = 1:iter

      # ---> A COMPLETER
      # ---> A COMPLETER

  end

  ##### Resultats de l'optimisation

  fopt = F
  gopt = G  
  xopt = x
  tcpu = time() - tic
    
  println()
  println("Iteration : ", kstar)
  println("Temps CPU : ", tcpu)
  println("Critere optimal : ", fopt)
  println("Norme du gradient : ", norm(G))

  # Visualisation de la convergence
  Visualg(logG, logP, cout)
    
  return fopt, gopt, xopt
    
end

In [ ]:
x0 = 0.1 * rand(n-md)
println()
println("MINIMISATION DU PROBLEME PRIMAL")
println()
println("ALGORITHME DE NEWTON A PAS VARIABLE")
copt, gopt, xopt = Newton_V(OraclePH, x0, 1.0)
qopt, zopt, fopt, popt = HydrauliqueP(xopt)
Verification(qopt, zopt, fopt, popt)

## II. Résolution du problème dual

In [ ]:
include("HydrauliqueD.jl")

### II.a On écrit les oracles pour le problème dual d'optimisation :

* **OracleDG** : calcul de la fonction et du gradient,
* **OracleDH** : calcul de la fonction du gradient et du Hessien.

In [ ]:
function OracleDG(pd)

  # ---> A COMPLETER
  # ---> A COMPLETER
    
  return F, G

end

In [ ]:
function OracleDH(pd)

  # ---> A COMPLETER
  # ---> A COMPLETER
    
  return F, G, H

end

### II.b On exécute tous les algorithmes d'optimisation déjà écrits

In [ ]:
x0 = 100.0 .+ rand(md)
println()
println("MINIMISATION DU PROBLEME DUAL")
println()
println("ALGORITHME DU GRADIENT A PAS VARIABLE")
copt, gopt, xopt = Gradient_V(OracleDG, x0, 5.0)
qopt, zopt, fopt, popt = HydrauliqueD(xopt)
Verification(qopt, zopt, fopt, popt)

In [ ]:
x0 = 100.0 .+ rand(md)
println()
println("MINIMISATION DU PROBLEME DUAL")
println()
println("ALGORITHME DU GRADIENT CONJUGUE")
copt, gopt, xopt = PolakRibiere(OracleDG, x0, 5.0)
qopt, zopt, fopt, popt = HydrauliqueD(xopt)
Verification(qopt, zopt, fopt, popt)

In [ ]:
x0 = 100 .+ rand(md)
println()
println("MINIMISATION DU PROBLEME DUAL")
println()
println("ALGORITHME DE QUASI-NEWTON")
copt, gopt, xopt = BFGS(OracleDG, x0, 1.0)
qopt, zopt, fopt, popt = HydrauliqueD(xopt)
Verification(qopt, zopt, fopt, popt)

In [ ]:
x0 = 100 .+ rand(md)
println()
println("MINIMISATION DU PROBLEME DUAL")
println()
println("ALGORITHME DE NEWTON A PAS VARIABLE")
copt, gopt, xopt = Newton_V(OracleDH, x0, 1.0)
qopt, zopt, fopt, popt = HydrauliqueD(xopt)
Verification(qopt, zopt, fopt, popt)

## III. Résolution de grands réseaux (facultatif)

### On charge dans l'environnement les données du problème

Ces données correspondent à un réseau de taille paramétrable.

In [ ]:
include("Probleme_P.jl")
include("Structures_S.jl")
println()
println("Tailles du reseau etudie")
println("Nombre de niveaux :", T)
println("Nombre de tuyaux  :", n)
println("Nombre de noeuds  :", m)

### III.a On écrit des oracles primal et dual avec Hessien creux

In [ ]:
function OraclePHS(qc)

  # ---> A COMPLETER
  # ---> A COMPLETER
            
  return F, G, H
    
end

In [ ]:
function OracleDHS(pd)

  # ---> A COMPLETER
  # ---> A COMPLETER
            
  return F, G, H
    
end

### III.b On écrit un algorithme de Newton exploitant le creux

In [ ]:
function Newton_S(Oracle, x0, alpha0)

  # ---> A COMPLETER
  # ---> A COMPLETER
    
  return fopt, gopt, xopt
    
end

### III.c On résoud le problème dans le primal et dans le dual

In [ ]:
x0 = 0.1 * rand(n-md)
println()
println("MINIMISATION DU PROBLEME PRIMAL DE GRANDE TAILLE")
println()
println("ALGORITHME DE NEWTON A PAS VARIABLE")
copt, gopt, xopt = Newton_S(OraclePHS, x0, 1.0)
qopt, zopt, fopt, popt = HydrauliqueP(xopt)
Verification(qopt, zopt, fopt, popt)

In [ ]:
x0 = 100 .+ rand(md)
println()
println("MINIMISATION DU PROBLEME DUAL DE GRANDE TAILLE")
println()
println("ALGORITHME DE NEWTON A PAS VARIABLE")
copt, gopt, xopt = Newton_S(OracleDHS, x0, 1.0)
qopt, zopt, fopt, popt = HydrauliqueD(xopt)
Verification(qopt, zopt, fopt, popt)